# 실험 목표
## calibration 끝난 후의 자기장 센서가 어떤 데이터를 주는지 확인 후, 이를 heading 추정을 위해 사용할 수 있을지 확인

# 실험 방법
## 실험 1
### 키스트 야외에서 calibration 한 후, 한바퀴를 돌며 자기장이 가르키는 자북이 어떻게 변하는지 관찰
## 실험 2
### 키스트 원내(L1)에서 calibration 한 후, 한바퀴를 돌며 자기장이 가르키는 자북이 어떻게 변하는지 관찰


In [42]:
import os
if "/content" in os.getcwd():
  !rm -rf WHere_codes/
  !git clone https://github.com/keenranger/WHere_codes
  os.chdir("/content/WHere_codes")
  !pip install -r requirements.txt

from PDR.modules.DataLoader import *
from PDR.modules.Walker import *
from PDR.modules.PlotlyPlotter import *
from PDR.modules.MagnetCalculator import *



import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from tqdm import tqdm
import plotly.graph_objects as go

## 실험 1의 calibration 이전 uncalibrated data를 plot

In [43]:
sensor_df = pd.read_csv("data/200716_mag03.csv", names=['experiment', 'time', 'accx', 'accy', 'accz', 'gyrox', 'gyroy',
                                                               'gyroz', 'magx', 'magy', 'magz', 'rot0', 'rot1', 'rot2', 'rot3', 'game0', 'game1', 'game2', 'game3', 'light','pressure', "x_uncalib", "y_uncalib","z_uncalib","x_bias","y_bias","z_bias"])
mag_df = sensor_df[['time','magx', 'magy', 'magz',"x_uncalib", "y_uncalib","z_uncalib","x_bias","y_bias","z_bias"]]
plot_magnet(mag_df, "before calibration").show()

## 실험 1 bias calibration 이후

In [44]:
bias_df = bias_calculator(mag_df)
mag_df = bias_calibrator(mag_df, bias_df)
plot_magnet(mag_df, "after bias calibration").show()


## 실험 1 scale calibration 이후

In [45]:
scale_df = scale_calculator(mag_df)
mag_df = scale_calibrator(mag_df, scale_df)
plot_magnet(mag_df, "after scale calibration")


## calibration 값들을 한바퀴 돈 실험에 적용

In [46]:
sensor_df = pd.read_csv("data/200716_mag04.csv", names=['experiment', 'time', 'accx', 'accy', 'accz', 'gyrox', 'gyroy',
                                                               'gyroz', 'magx', 'magy', 'magz', 'rot0', 'rot1', 'rot2', 'rot3', 'game0', 'game1', 'game2', 'game3', 'light','pressure', "x_uncalib", "y_uncalib","z_uncalib","x_bias","y_bias","z_bias"])
mag_df = sensor_df[['time','magx', 'magy', 'magz',"x_uncalib", "y_uncalib","z_uncalib","x_bias","y_bias","z_bias"]]
mag_df = bias_calibrator(mag_df, bias_df)
mag_df = scale_calibrator(mag_df, scale_df)
plot_magnet(mag_df, "after calibration").show()


## Calibration 후 시간에 따른 x,y,z의 변화

In [47]:
mag_df

time       magx       magy       magz  x_uncalib  y_uncalib  \
0      1594888355829  15.881161 -32.182580 -34.877472  15.536804 -32.036212   
1      1594888355849  16.204853 -32.459908 -35.958650  14.805404 -30.138451   
2      1594888355869  13.898495 -31.022110 -34.860382  13.554138 -30.788177   
3      1594888355889  15.298519 -32.600037 -36.592026  14.954162 -32.485172   
4      1594888355909  15.422764 -30.439964 -34.507103  15.078408 -30.162111   
...              ...        ...        ...        ...        ...        ...   
10337  1594888562569  17.756844 -33.476738 -34.122986  17.352208 -33.608002   
10338  1594888562589  17.569244 -35.099700 -32.502014  17.164608 -35.353429   
10339  1594888562609  15.445122 -35.530045 -33.472350  15.040488 -35.816247   
10340  1594888562629  16.219475 -34.794548 -33.891853  15.814838 -35.025249   
10341  1594888562650  16.212220 -34.508980 -33.419823  15.807588 -34.718131   

       z_uncalib     x_bias     y_bias     z_bias  
0     -34.555100  58.174305 -42.539963 -46.716248  
1     -36.065638  58.174305 -42.539963 -46.716248  
2     -34.537604  58.174305 -42.539963 -46.716248  
3     -36.310424  58.174305 -42.539963 -46.716248  
4     -34.175922  58.174305 -42.539963 -46.716248  
...          ...        ...        ...        ...  
10337 -33.801526  58.114030 -42.707314 -46.734665  
10338 -32.142008  58.114030 -42.707314 -46.734665  
10339 -33.135419  58.114030 -42.707314 -46.734665  
10340 -33.564899  58.114030 -42.707314 -46.734665  
10341 -33.081644  58.114030 -42.707314 -46.734665  

[10342 rows x 10 columns]

In [48]:
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=mag_df['time'], 
    y=mag_df['x_uncalib'],
    name = 'x'))
fig.add_trace(go.Scatter(
    x=mag_df['time'], 
    y=mag_df['y_uncalib'],
    name = 'y'))
fig.add_trace(go.Scatter(
    x=mag_df['time'],
    y=mag_df['z_uncalib'],
    name='z'))

## Calibration 후 시간에 따른 heading 변화

In [49]:
magnet_heading = np.arctan2(mag_df['y_uncalib'], mag_df['x_uncalib'])*180/np.pi
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=mag_df['time'], 
    y=magnet_heading,
    name = 'heading'))

## 실험 2의 calibration 이전 uncalibrated data를 plot

In [50]:
sensor_df = pd.read_csv("data/200716_mag01.csv", names=['experiment', 'time', 'accx', 'accy', 'accz', 'gyrox', 'gyroy',
                                                               'gyroz', 'magx', 'magy', 'magz', 'rot0', 'rot1', 'rot2', 'rot3', 'game0', 'game1', 'game2', 'game3', 'light', "x_uncalib", "y_uncalib","z_uncalib","x_bias","y_bias","z_bias"])
mag_df = sensor_df[['time','magx', 'magy', 'magz',"x_uncalib", "y_uncalib","z_uncalib","x_bias","y_bias","z_bias"]]
plot_magnet(mag_df, "before calibration").show()

## 실험 2 bias calibration 이후

In [51]:
bias_df = bias_calculator(mag_df)
mag_df = bias_calibrator(mag_df, bias_df)
plot_magnet(mag_df, "after bias calibration").show()


## 실험 2의 scale calibration 이후

In [52]:
scale_df = scale_calculator(mag_df)
mag_df = scale_calibrator(mag_df, scale_df)
plot_magnet(mag_df, "after scale calibration")


## calibration 값들을 한바퀴 돈 실험에 적용

In [53]:
sensor_df = pd.read_csv("data/200716_mag02.csv", names=['experiment', 'time', 'accx', 'accy', 'accz', 'gyrox', 'gyroy',
                                                               'gyroz', 'magx', 'magy', 'magz', 'rot0', 'rot1', 'rot2', 'rot3', 'game0', 'game1', 'game2', 'game3', 'light', "x_uncalib", "y_uncalib","z_uncalib","x_bias","y_bias","z_bias"])
mag_df = sensor_df[['time','magx', 'magy', 'magz',"x_uncalib", "y_uncalib","z_uncalib","x_bias","y_bias","z_bias"]]
mag_df = bias_calibrator(mag_df, bias_df)
mag_df = scale_calibrator(mag_df, scale_df)
plot_magnet(mag_df, "after calibration").show()

## calibraton 후 시간에 따른 x, y, z 의 변화

In [54]:
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=mag_df['time'], 
    y=mag_df['x_uncalib'],
    name = 'x'))
fig.add_trace(go.Scatter(
    x=mag_df['time'], 
    y=mag_df['y_uncalib'],
    name = 'y'))
fig.add_trace(go.Scatter(
    x=mag_df['time'],
    y=mag_df['z_uncalib'],
    name='z'))

## calibration 후 시간에 따른 heading의 변화

In [55]:
magnet_heading = np.arctan2(mag_df['y_uncalib'], mag_df['x_uncalib'])*180/np.pi
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=mag_df['time'], 
    y=magnet_heading,
    name = 'heading'))